In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import numpy as np
import torch
import pandas as pd
import torchvision
import torchvision.transforms as transforms
from torch.utils.data import DataLoader, Dataset
import matplotlib.pyplot as plt
import protector as protect
from utils.cli_utils import softmax_ent

from tent import Tent, configure_model, collect_params
from typing import Sequence, Tuple, Dict, Optional
import argparse

from sklearn.manifold import TSNE
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt

from utilities import *  ## created by me
from plotting import *  ## created by me

In [3]:
CORRUPTIONS = (
    "shot_noise",
    "motion_blur",
    "snow",
    "pixelate",
    "gaussian_noise",
    "defocus_blur",
    "brightness",
    "fog",
    "zoom_blur",
    "frost",
    "glass_blur",
    "impulse_noise",
    "contrast",
    "jpeg_compression",
    "elastic_transform",
)

In [4]:
## ENTER PARAMETERS ##

# Manual settings for arguments
args = type("Args", (), {})()  # Create a simple namespace object
args.device = "cpu"  # Change this manually as needed
args.method = "none"  # Options: 'none' or 'tent'
args.corruption = "gaussian_noise"  # Choose from CORRUPTIONS
args.all_corruptions = False  # Set to True to test all corruptions
args.n_examples = 1000
args.batch_size = 64

# Set torch seed for replicability (don't know if this preserves consistency when using different devices)
torch.manual_seed(42)

Basic set up where we load clean CIFAR-10 and then test on corrupted version. This is a good reference to get a feel for how everyting works together.

In [5]:
# Dynamically set device to best available option
device = torch.device("cuda" if torch.cuda.is_available() else "mps" if torch.backends.mps.is_available() else "cpu")

# Define normalization transform using CIFAR-10 mean and std values
transform = transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2471, 0.2435, 0.2616))

# Load pre-trained model and move to appropriate device
print("🚀 Loading model...")
model = get_model(args.method, device)

# Load clean CIFAR-10 test data to compute source entropies
print("📦 Loading clean CIFAR-10 as source entropy")
clean_ds = torchvision.datasets.CIFAR10(
    root="./data", train=False, download=True, transform=transforms.Compose([transforms.ToTensor(), transform])
)
clean_loader = DataLoader(clean_ds, batch_size=args.batch_size, shuffle=False)
source_ents, _, _, _ = evaluate(model, clean_loader, device)

# Initialize protector with source entropies for shift detection
protector = protect.get_protector_from_ents(
    source_ents, argparse.Namespace(gamma=1 / (8 * np.sqrt(3)), eps_clip=1.8, device=device)
)

# --- Label Shift Severity Sweep ---
label_shift_severities = {
    "none": list(range(10)),  # no actual shift
    "medium": list(range(5)),  # moderate shift
    "severe": [0, 1, 2],  # strong shift
    "extreme": [0],  # extreme shift
}

entropy_streams = {}
accs = {}
logits_list_dict = {}
logits_labels_dict = {}

for severity_name, keep_classes in label_shift_severities.items():
    print(f"🔎 Evaluating label shift severity: {severity_name}")
    x, y = load_cifar10_label_shift(keep_classes=keep_classes, n_examples=8000, shift_point=4000)
    dataset = BasicDataset(x, y, transform=transform)
    loader = DataLoader(dataset, batch_size=args.batch_size, shuffle=False)

    ents, acc, logits_list, labels_list = evaluate(model, loader, device)

    key = f"label_shift_{severity_name}"
    entropy_streams[key] = ents
    accs[key] = acc
    logits_list_dict[key] = logits_list
    logits_labels_dict[key] = labels_list

# Run martingale-based shift detection
results = run_martingale(entropy_streams, protector)

# Print results
print("\n📊 Accuracy under label shift severities:")
for key, value in accs.items():
    print(f"{key}: {value * 100:.2f}%")


🚀 Loading model...


Using cache found in /Users/louis/.cache/torch/hub/chenyaofo_pytorch-cifar-models_master


📦 Loading clean CIFAR-10 as source entropy
Files already downloaded and verified


Evaluating: 100%|██████████| 157/157 [00:02<00:00, 55.76it/s]
2025-05-22 14:55:45.162 | INFO     | protector:get_protector_from_ents:146 - creating protector from ents
2025-05-22 14:55:45.169 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 14:55:45.172 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


🔎 Evaluating label shift severity: none


...

🔎 Evaluating label shift severity: severe


Evaluating: 100%|██████████| 110/110 [00:01<00:00, 70.33it/s]


🔎 Evaluating label shift severity: extreme


Evaluating: 100%|██████████| 79/79 [00:01<00:00, 62.99it/s]



📊 Accuracy under label shift severities:
label_shift_none: 93.17%
label_shift_medium: 92.79%
label_shift_severe: 93.41%
label_shift_extreme: 93.28%


In [ ]:
# Set up the plot
plt.figure(figsize=(12, 6))

# Plot entropy streams for each severity level
plt.plot(entropy_streams["label_shift_none"], label="None", alpha=0.7)
plt.plot(entropy_streams["label_shift_medium"], label="Medium", alpha=0.7)
plt.plot(entropy_streams["label_shift_severe"], label="Severe", alpha=0.7)

# Add vertical line at shift point (assuming shift point at 4000/batch_size)
shift_point = 4000
plt.axvline(x=shift_point, color="r", linestyle="--", alpha=0.5, label="Shift Point")

# Customize the plot
plt.xlabel("Batch Index")
plt.ylabel("Entropy")
plt.title("Entropy Streams for Different Label Shift Severities")
plt.legend()
plt.grid(True, alpha=0.3)

plt.tight_layout()
plt.show()

In [ ]:
label_shift_levels = {
    "mild": list(range(10)),
    "medium": list(range(5)),
    "severe": [0, 1, 2],
    "test": [6, 7, 8],
    "test2": [3, 4, 5],
    "extreme": [0],
}

accs, entropy_streams, logits_list_dict, logits_labels_dict = {}, {}, {}, {}

for severity_name, keep_classes in label_shift_levels.items():
    print(f"🔎 Label shift severity: {severity_name}")

    loader, is_clean, labels = load_clean_then_label_shift_sequence(
        keep_classes=keep_classes,
        n_examples=8000,
        shift_point=4000,
        data_dir="./data/cifar-10-batches-py",
        transform=transform,
        batch_size=args.batch_size,
    )

    ents, acc, logits_list, labels_list = evaluate(model, loader, device)

    key = f"labelshift_{severity_name}"
    entropy_streams[key] = ents
    accs[key] = acc
    logits_list_dict[key] = logits_list
    logits_labels_dict[key] = labels_list

# Run martingale
results = run_martingale(entropy_streams, protector)

# Add accuracy over time
for severity_name in label_shift_levels:
    key = f"labelshift_{severity_name}"
    acc_time = compute_accuracy_over_time_from_logits(logits_list_dict[key], logits_labels_dict[key])
    results[key]["accs"] = acc_time


In [ ]:
# Create dictionaries to store values for each label shift severity
log_sj_dict = {}
epsilons_dict = {}
accuracies_dict = {}
entropy_dict = {}

# Extract values for each severity level
for severity in label_shift_levels.keys():
    key = f"labelshift_{severity}"
    if key in results:
        log_sj_dict[severity] = results[key]["log_sj"]
        epsilons_dict[severity] = results[key]["eps"]
        accuracies_dict[severity] = results[key]["accs"]
        entropy_dict[severity] = entropy_streams[key]

# Plot the combined results
plot_combined_martingale_accuracy_severity(
    log_sj_dict,
    epsilons_dict,
    accuracies_dict,
    entropy_dict=entropy_dict,
    batch_size=64,
    title="Label Shift Comparison Across Severities",
)


In [ ]:
max(results["labelshift_test"]["log_sj"])

In [ ]:
np.log(100)

In [ ]:
detection_delays = compute_detection_delays_from_threshold(log_sj_dict)

# Call the function to plot detection delays
plot_detection_delays(detection_delays)

In [ ]:
import seaborn as sns
import matplotlib.pyplot as plt

for k in entropy_streams:
    sns.kdeplot(entropy_streams[k], label=k)

plt.title("Entropy Distribution by Label Subset")
plt.xlabel("Entropy")
plt.ylabel("Density")
plt.legend()
plt.grid(True)
plt.show()


In [ ]:
fpr_by_size

In [ ]:
from itertools import combinations
import numpy as np

fpr_by_size = {}  # ← new: store FPR per class‑set size

for num_classes in [1]:
    candidate_class_sets = list(combinations(range(10), num_classes))

    entropy_peaks = {}
    threshold_crossed = {}

    for subset in candidate_class_sets:
        print(f"Evaluating label shift ({num_classes}-class): {subset}")

        # 1) Load synthetic label‑shift stream
        x, y = load_cifar10_label_shift(keep_classes=subset, n_examples=8000, shift_point=4000)
        dataset = BasicDataset(x, y, transform=transform)
        loader = DataLoader(dataset, batch_size=args.batch_size, shuffle=False)

        # 2) Forward pass
        ents, acc, logits_list, labels_list = evaluate(model, loader, device)

        # 3) Martingale test
        key = f"labelshift_{num_classes}cls_{'_'.join(map(str, subset))}"
        result = run_martingale({key: ents}, protector)[key]

        # 4) Record stats
        entropy_peaks[key] = np.max(ents)
        threshold_crossed[key] = np.max(result["log_sj"]) > np.log(100)

    # --- compute per‑size false‑positive rate -------------------------
    n_tests = len(threshold_crossed)
    n_crossed = sum(threshold_crossed.values())
    fpr = n_crossed / n_tests
    fpr_by_size[num_classes] = fpr  # save for later use

    print(f"\n➡️  {n_crossed} / {n_tests} ({num_classes}-class) shifts triggered detection  – FPR = {fpr:.3f}\n")

# ----------------------------------------------------------------------
# Now fpr_by_size contains something like {2: 0.20, 3: 0.35, ...}
# You can save it to disk, log to WandB, etc.


In [ ]:
from collections import defaultdict
import random


class PBRSBuffer:
    def __init__(self, capacity=64, num_classes=10):
        self.capacity = capacity
        self.num_classes = num_classes
        self.target_per_class = capacity // num_classes
        self.buffer = []
        self.label_counts = defaultdict(int)

    def accept(self, y_hat):
        # Always accept if there's room
        if len(self.buffer) < self.capacity:
            return True
        # Reject if class is already full
        if self.label_counts[y_hat] >= self.target_per_class:
            return False
        return True

    def add(self, x, entropy, y_hat):
        if len(self.buffer) >= self.capacity:
            for i, (_, _, label) in enumerate(self.buffer):
                if self.label_counts[label] > self.target_per_class:
                    self.label_counts[label] -= 1
                    del self.buffer[i]
                    break
            else:
                removed = self.buffer.pop(0)
                self.label_counts[removed[2]] -= 1

        self.buffer.append((x, entropy, y_hat))
        self.label_counts[y_hat] += 1

    def full(self):
        return len(self.buffer) >= self.capacity

    def get_entropies(self):
        return [entry[1] for entry in self.buffer]

    def reset(self):
        self.buffer = []
        self.label_counts = defaultdict(int)

In [ ]:
from itertools import combinations
import numpy as np

fpr_by_size = {}  # ← new: store FPR per class‑set size

for num_classes in [3]:
    candidate_class_sets = list(combinations(range(10), num_classes))

    entropy_peaks = {}
    threshold_crossed = {}

    for subset in candidate_class_sets:
        print(f"Evaluating label shift ({num_classes}-class): {subset}")

        # 1) Load synthetic label‑shift stream
        x, y = load_cifar10_label_shift(keep_classes=subset, n_examples=8000, shift_point=4000)
        dataset = BasicDataset(x, y, transform=transform)
        loader = DataLoader(dataset, batch_size=args.batch_size, shuffle=False)

        # Step 2: Forward pass with PBRS buffering
        confidence_threshold = 0.8  # You can tune this

        buffer = PBRSBuffer(capacity=512, num_classes=num_classes)
        with torch.no_grad():
            for x_batch, _ in loader:
                x_batch = x_batch.to(device)
                logits = model(x_batch)
                probs = torch.softmax(logits, dim=1)
                entropies = -torch.sum(probs * torch.log(probs + 1e-8), dim=1)
                pseudo_labels = torch.argmax(probs, dim=1)
                max_probs = torch.max(probs, dim=1).values  # ← get model confidence

                # Add only confident, accepted samples to buffer
                for entropy, y_hat, confidence in zip(
                    entropies.cpu().tolist(), pseudo_labels.cpu().tolist(), max_probs.cpu().tolist()
                ):
                    if confidence > confidence_threshold and buffer.accept(y_hat):
                        buffer.add(None, entropy, y_hat)

        # Step 3: Run martingale test on buffered entropies
        key = f"labelshift_{num_classes}cls_{'_'.join(map(str, subset))}_PBRS"

        ents = buffer.get_entropies()
        result = run_martingale({key: np.array(ents)}, protector)[key]

        # Step 4: Store stats
        entropy_peaks[key] = np.max(ents)
        threshold_crossed[key] = np.max(result["log_sj"]) > np.log(100)

    # --- compute per‑size false‑positive rate -------------------------
    n_tests = len(threshold_crossed)
    n_crossed = sum(threshold_crossed.values())
    fpr = n_crossed / n_tests
    fpr_by_size[num_classes] = fpr  # save for later use

    print(f"\n➡️  {n_crossed} / {n_tests} ({num_classes}-class) shifts triggered detection  – FPR = {fpr:.3f}\n")

In [ ]:
## ENTER PARAMETERS ##

# Manual settings for arguments
args = type("Args", (), {})()  # Create a simple namespace object
args.device = "cpu"  # Change this manually as needed
args.method = "none"  # Options: 'none' or 'tent'
args.corruption = "gaussian_noise"  # Choose from CORRUPTIONS
args.all_corruptions = False  # Set to True to test all corruptions
args.n_examples = 1000
args.batch_size = 64

# Set torch seed for replicability (don't know if this preserves consistency when using different devices)
torch.manual_seed(42)

In [ ]:
def confidence_accept(conf, threshold=0.8, softness=15):
    """
    Accept sample with probability based on confidence.
    - High confidence → near-certain acceptance
    - Medium confidence → partial acceptance
    - Low confidence → mostly rejected
    """
    prob = 1 / (1 + np.exp(-softness * (conf - threshold)))
    return random.random() < prob

In [ ]:
def confidence_accept(conf, threshold=0.8, softness=15):
    """
    Accept sample with probability based on confidence.
    - High confidence → near-certain acceptance
    - Medium confidence → partial acceptance
    - Low confidence → mostly rejected
    """
    prob = 1 / (1 + np.exp(-softness * (conf - threshold)))
    return random.random() < prob


accs, entropy_streams, logits_list_dict, logits_labels_dict = {}, {}, {}, {}
results = {}
corruptions = CORRUPTIONS if args.all_corruptions else [args.corruption]

use_pbrs = True
confidence_threshold = 0.8  # You can tune this

for corruption in corruptions:
    for severity in range(1, 6):
        print(f"🔎 {corruption} severity {severity} (clean → corrupt)")

        # Load clean-to-corrupt stream
        loader, is_clean, labels = load_clean_then_corrupt_sequence(
            corruption=corruption,
            severity=severity,
            n_examples=4000,
            data_dir="./data",
            transform=transform,
            batch_size=args.batch_size,
        )

        if use_pbrs:
            buffer = PBRSBuffer(capacity=512, num_classes=10)

        logits_list = []
        labels_list = []
        entropy_list = []

        with torch.no_grad():
            for x_batch, y_batch in loader:
                x_batch, y_batch = x_batch.to(device), y_batch.to(device)
                logits = model(x_batch)
                probs = torch.softmax(logits, dim=1)
                entropies = -torch.sum(probs * torch.log(probs + 1e-8), dim=1)
                pseudo_labels = torch.argmax(probs, dim=1)
                max_probs = torch.max(probs, dim=1).values

                for entropy, y_hat, conf in zip(
                    entropies.cpu().tolist(), pseudo_labels.cpu().tolist(), max_probs.cpu().tolist()
                ):
                    if use_pbrs:
                        if confidence_accept(conf, threshold=0.8, softness=15) and buffer.accept(y_hat):
                            buffer.add(None, entropy, y_hat)
                    else:
                        entropy_list.append(entropy)

                logits_list.append(logits.cpu())
                labels_list.append(y_batch.cpu())

        key = f"{corruption}_s{severity}"

        # Store entropy stream
        ents = np.array(buffer.get_entropies()) if use_pbrs else np.array(entropy_list)
        entropy_streams[key] = ents
        logits_list_dict[key] = logits_list
        logits_labels_dict[key] = labels_list


# Run martingale detection on all entropy streams
results = run_martingale(entropy_streams, protector)

# Compute accuracy over time
for corruption in corruptions:
    for severity in range(1, 6):
        key = f"{corruption}_s{severity}"
        accs = compute_accuracy_over_time_from_logits(logits_list_dict[key], logits_labels_dict[key])
        results[key]["accs"] = accs

In [ ]:
# Get max log_sj values for each severity level
max_log_sj = {}
for severity in results:
    max_log_sj[severity] = max(results[severity]["log_sj"])
    print(f"Max log_sj for {severity}: {max_log_sj[severity]}")

# Sort by severity level for cleaner display
sorted_max_log_sj = dict(sorted(max_log_sj.items()))

# Print results
for severity, value in sorted_max_log_sj.items():
    print(f"{severity}: {value:.2f}")

In [ ]:
# Get max log_sj values for each severity level
max_log_sj = {}
for severity in results:
    max_log_sj[severity] = max(results[severity]["log_sj"])
    print(f"Max log_sj for {severity}: {max_log_sj[severity]}")

# Sort by severity level for cleaner display
sorted_max_log_sj = dict(sorted(max_log_sj.items()))

# Print results
for severity, value in sorted_max_log_sj.items():
    print(f"{severity}: {value:.2f}")

In [ ]:
np.log(100)

In [ ]:
# Create dictionaries to store values for each severity
log_sj_dict = {}
epsilons_dict = {}
accuracies_dict = {}

# Extract values for each severity level
for severity in range(1, 6):
    key = f"gaussian_noise_s{severity}"
    if key in results:
        log_sj_dict[key] = results[key]["log_sj"]
        epsilons_dict[key] = results[key]["eps"]
        accuracies_dict[key] = results[key]["accs"]

# Plot the combined results
if use_pbrs:
    plot_combined_martingale_accuracy_severity_pbrs(
        log_sj_dict,
        epsilons_dict,
        accuracies_dict,
        entropy_dict=entropy_streams,
        batch_size=64,
        buffer_size=256,
        title="Gaussian Noise Comparison Across Severities (PBRS)",
    )
else:
    plot_combined_martingale_accuracy_severity(
        log_sj_dict,
        epsilons_dict,
        accuracies_dict,
        entropy_dict=entropy_streams,
        batch_size=64,
        title="Gaussian Noise Comparison Across Severities",
    )

Implement Component 2: weighted CDF

In [ ]:
from weighted_cdf import *
from protector import *

In [ ]:
# Dynamically set device to best available option
device = torch.device("cuda" if torch.cuda.is_available() else "mps" if torch.backends.mps.is_available() else "cpu")

# Define normalization transform using CIFAR-10 mean and std values
transform = transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2471, 0.2435, 0.2616))

# Load pre-trained model and move to appropriate device
print("🚀 Loading model...")
model = get_model(args.method, device)

In [ ]:
from torch.utils.data import DataLoader, Subset
from torchvision.transforms import Compose, ToTensor

# 1. Wrap full dataset
# 1) Load synthetic label‑shift stream

split = 4000
x, y = load_cifar10_label_shift(keep_classes=subset, n_examples=8000, shift_point=split)
full_dataset = BasicDataset(x, y, transform=transform)

# 2. Split into clean and shifted
clean_loader = DataLoader(Subset(full_dataset, range(0, split)), batch_size=args.batch_size, shuffle=False)

test_loader = DataLoader(
    Subset(full_dataset, range(split, len(full_dataset))), batch_size=args.batch_size, shuffle=False
)

# 1. Estimate p_s from clean CIFAR-10
p_s = estimate_label_distribution(model, clean_loader, device)

# 2. Estimate p_t and collect pseudo-labels on test stream
p_t, _ = estimate_pseudo_label_distribution(model, test_loader, device)
_, source_pseudo_labels = estimate_pseudo_label_distribution(model, clean_loader, device)

# 3. Collect entropies on clean source set
# source_ents = compute_entropies(model, clean_loader, device)  # or reuse from before
source_ents = []
source_pseudo_labels = []

with torch.no_grad():
    for x, _ in clean_loader:
        x = x.to(device)
        logits = model(x)
        probs = torch.softmax(logits, dim=1)
        entropy = -torch.sum(probs * torch.log(probs + 1e-8), dim=1)
        y_hat = torch.argmax(probs, dim=1)

        source_ents.extend(entropy.cpu().tolist())
        source_pseudo_labels.extend(y_hat.cpu().tolist())

# 4. Create weighted CDF object
weighted_cdf = WeightedCDF(entropies=source_ents, pseudo_labels=source_pseudo_labels, p_s=p_s.numpy(), p_t=p_t.numpy())
protector = protect.get_weighted_protector_from_ents(
    source_ents,
    source_pseudo_labels,
    p_s,
    p_t,
    argparse.Namespace(gamma=1 / (8 * np.sqrt(3)), eps_clip=1.8, device=device),
)

#### Weighted CDF with BBSE weights

In [ ]:
from torch.utils.data import DataLoader, Subset
from torchvision.transforms import Compose, ToTensor
from weighted_cdf_bbse import BBSEWeightedCDF, estimate_shift_weights

# 1. Wrap full dataset
# 1) Load synthetic label‑shift stream

split = 4000
x, y = load_cifar10_label_shift(keep_classes=subset, n_examples=8000, shift_point=split)
full_dataset = BasicDataset(x, y, transform=transform)

# 2. Split into clean and shifted
clean_loader = DataLoader(Subset(full_dataset, range(0, split)), batch_size=args.batch_size, shuffle=False)

test_loader = DataLoader(
    Subset(full_dataset, range(split, len(full_dataset))), batch_size=args.batch_size, shuffle=False
)

# nice wrapper function takes care of evertyhing
w, p_s, p_t_true, p_t_pred = estimate_shift_weights(model, clean_loader, test_loader, device)

# 3. Collect entropies on clean source set
# Could probably integrate entropy calculation into estimate_shift_weights for efficiency
source_ents = compute_entropies(model, clean_loader, device)  # or reuse from before

# source_ents = []
# source_pseudo_labels = []

# with torch.no_grad():
#     for x, _ in clean_loader:
#         x = x.to(device)
#         logits = model(x)
#         probs = torch.softmax(logits, dim=1)
#         entropy = -torch.sum(probs * torch.log(probs + 1e-8), dim=1)
#         #y_hat = torch.argmax(probs, dim=1)

#         source_ents.extend(entropy.cpu().tolist())
#         #source_pseudo_labels.extend(y_hat.cpu().tolist())

# 4. Create weighted CDF object
weighted_cdf = BBSEWeightedCDF(
    entropies=source_ents,
    pseudo_labels=pseudo_labels,
    weights=weights,
)

protector = protect.get_weighted_protector_from_ents(
    source_ents,
    source_pseudo_labels,
    p_s,
    p_t,
    argparse.Namespace(gamma=1 / (8 * np.sqrt(3)), eps_clip=1.8, device=device),
)

False positive rate

In [ ]:
from itertools import combinations
import numpy as np
import argparse
import torch
from torch.utils.data import DataLoader, Subset
from weighted_cdf import *

fpr_by_size = {}

for num_classes in [2]:  # Adjust as needed
    candidate_class_sets = list(combinations(range(10), num_classes))
    entropy_peaks = {}
    threshold_crossed = {}

    for subset in candidate_class_sets[:3]:
        print(f"\n🔎 Evaluating label shift ({num_classes}-class): {subset}")

        split = 4000

        # 1) Load clean source stream using only this subset of classes
        x_src, y_src = load_cifar10_label_shift(keep_classes=subset, n_examples=8000, shift_point=split)
        source_dataset = BasicDataset(x_src, y_src, transform=transform)

        source_loader = DataLoader(Subset(source_dataset, range(0, split)), batch_size=args.batch_size, shuffle=False)

        # 2) Estimate p_s and collect source entropies + pseudo-labels
        p_s = estimate_label_distribution(model, source_loader, device)

        source_ents = []
        source_pseudo_labels = []
        with torch.no_grad():
            for x_batch, _ in source_loader:
                x_batch = x_batch.to(device)
                logits = model(x_batch)
                probs = torch.softmax(logits, dim=1)
                entropy = -torch.sum(probs * torch.log(probs + 1e-8), dim=1)
                y_hat = torch.argmax(probs, dim=1)

                source_ents.extend(entropy.cpu().tolist())
                source_pseudo_labels.extend(y_hat.cpu().tolist())

        # 3) Load label-shifted stream (same subset)
        x_shift, y_shift = load_cifar10_label_shift(keep_classes=subset, n_examples=8000, shift_point=split)
        full_dataset = BasicDataset(x_shift, y_shift, transform=transform)

        test_loader = DataLoader(
            Subset(full_dataset, range(split, len(full_dataset))), batch_size=args.batch_size, shuffle=False
        )

        # 4) Estimate p_t from shifted half of the stream
        p_t, _ = estimate_pseudo_label_distribution(model, test_loader, device)

        mask = torch.tensor([i in subset for i in range(10)], dtype=torch.bool)

        p_s = p_s * mask
        p_s /= p_s.sum() + 1e-8

        p_t = p_t * mask
        p_t /= p_t.sum() + 1e-8

        # 5) Create weighted protector
        protector = protect.get_weighted_protector_from_ents(
            source_ents,
            source_pseudo_labels,
            p_s,
            p_t,
            argparse.Namespace(gamma=1 / (8 * np.sqrt(3)), eps_clip=1.8, device=device),
        )

        # 6) Evaluate full test stream and run martingale
        loader = DataLoader(full_dataset, batch_size=args.batch_size, shuffle=False)
        ents, acc, logits_list, labels_list = evaluate(model, loader, device)

        key = f"labelshift_{num_classes}cls_{'_'.join(map(str, subset))}"
        result = run_martingale({key: ents}, protector)[key]

        # 7) Record statistics
        entropy_peaks[key] = np.max(ents)
        threshold_crossed[key] = np.max(result["log_sj"]) > np.log(100)

        print("Subset:", subset)
        print("p_s:", p_s.numpy())
        print("p_t:", p_t.numpy())
        print("min p_s:", p_s.min().item(), "min p_t:", p_t.min().item())

    # 8) Calculate and store FPR
    n_tests = len(threshold_crossed)
    n_crossed = sum(threshold_crossed.values())
    fpr = n_crossed / n_tests
    fpr_by_size[num_classes] = fpr

    print(f"\n➡️ {n_crossed} / {n_tests} ({num_classes}-class) shifts triggered detection — FPR = {fpr:.3f}\n")

# fpr_by_size now holds clean, valid FPRs per class subset size.

##### BBSE False positives

In [ ]:
from itertools import combinations
import numpy as np
import argparse
import torch
from torch.utils.data import DataLoader, Subset
from weighted_cdf_bbse import BBSEWeightedCDF, estimate_shift_weights

fpr_by_size = {}

for num_classes in [2]:  # Adjust as needed
    candidate_class_sets = list(combinations(range(10), num_classes))
    entropy_peaks = {}
    threshold_crossed = {}

    for subset in candidate_class_sets[:3]:
        print(f"\n🔎 Evaluating label shift ({num_classes}-class): {subset}")

        split = 4000

        # 1) Load clean source stream using only this subset of classes
        x_src, y_src = load_cifar10_label_shift(keep_classes=subset, n_examples=8000, shift_point=split)
        source_dataset = BasicDataset(x_src, y_src, transform=transform)

        source_loader = DataLoader(Subset(source_dataset, range(0, split)), batch_size=args.batch_size, shuffle=False)

        source_ents = []
        source_labels = []
        with torch.no_grad():
            for x_batch, labels in source_loader:
                x_batch = x_batch.to(device)
                logits = model(x_batch)
                probs = torch.softmax(logits, dim=1)
                entropy = -torch.sum(probs * torch.log(probs + 1e-8), dim=1)
                y_hat = torch.argmax(probs, dim=1)

                source_ents.extend(entropy.cpu().tolist())
                # We have access to ground truth labels for init of CDF, so we are using them here
                source_labels.extend(labels.cpu().tolist())

        # 3) Load label-shifted stream (same subset)
        x_shift, y_shift = load_cifar10_label_shift(keep_classes=subset, n_examples=8000, shift_point=split)
        full_dataset = BasicDataset(x_shift, y_shift, transform=transform)

        test_loader = DataLoader(
            Subset(full_dataset, range(split, len(full_dataset))), batch_size=args.batch_size, shuffle=False
        )

        # 4) Estimate p_t from shifted half of the stream
        weights, p_s, p_t_true, p_t_pred = estimate_shift_weights(model, source_loader, test_loader, device)
        print(f"p_true: {p_t_true}")

        # 5) Create weighted protector
        protector = protect.get_bbse_weighted_protector_from_ents(
            source_ents,
            source_labels,
            weights,
            argparse.Namespace(gamma=1 / (8 * np.sqrt(3)), eps_clip=1.8, device=device),
        )

        # 6) Evaluate full test stream and run martingale
        loader = DataLoader(full_dataset, batch_size=args.batch_size, shuffle=False)
        ents, acc, logits_list, labels_list = evaluate(model, loader, device)

        key = f"labelshift_{num_classes}cls_{'_'.join(map(str, subset))}"
        result = run_martingale({key: ents}, protector)[key]

        # 7) Record statistics
        entropy_peaks[key] = np.max(ents)
        threshold_crossed[key] = np.max(result["log_sj"]) > np.log(100)

        print("Subset:", subset)
        print("p_s:", p_s.numpy())
        # TODO: LOUIS: Not sure if we should be using the original preds or the transformed ones
        print("p_t:", p_t_true.numpy())
        print("min p_s:", p_s.min().item(), "min p_t:", p_t_true.min().item())

    # 8) Calculate and store FPR
    n_tests = len(threshold_crossed)
    n_crossed = sum(threshold_crossed.values())
    fpr = n_crossed / n_tests
    fpr_by_size[num_classes] = fpr

    print(f"\n➡️ {n_crossed} / {n_tests} ({num_classes}-class) shifts triggered detection — FPR = {fpr:.3f}\n")

# fpr_by_size now holds clean, valid FPRs per class subset size.

#### BBSE ODS False Positives

In [ ]:
from itertools import combinations
import numpy as np
import argparse
import torch
from torch.utils.data import DataLoader, Subset
from weighted_cdf_bbse_ods import (
    BBSEODSWeightedCDF,
    estimate_confusion_matrix,
    estimate_target_distribution_from_preds,
)

fpr_by_size = {}

for num_classes in [2]:  # Adjust as needed
    candidate_class_sets = list(combinations(range(10), num_classes))
    entropy_peaks = {}
    threshold_crossed = {}

    for subset in candidate_class_sets[:3]:
        print(f"\n🔎 Evaluating label shift ({num_classes}-class): {subset}")

        split = 4000

        # 1) Load clean source stream using only this subset of classes
        x_src, y_src = load_cifar10_label_shift(keep_classes=subset, n_examples=8000, shift_point=split)
        source_dataset = BasicDataset(x_src, y_src, transform=transform)

        source_loader = DataLoader(Subset(source_dataset, range(0, split)), batch_size=args.batch_size, shuffle=False)

        source_ents = []
        source_labels = []
        with torch.no_grad():
            for x_batch, labels in source_loader:
                x_batch = x_batch.to(device)
                logits = model(x_batch)
                probs = torch.softmax(logits, dim=1)
                entropy = -torch.sum(probs * torch.log(probs + 1e-8), dim=1)
                y_hat = torch.argmax(probs, dim=1)

                source_ents.extend(entropy.cpu().tolist())
                # We have access to ground truth labels for init of CDF, so we are using them here
                source_labels.extend(labels.cpu().tolist())

        # BBSE: Estimate confusion matrix and p_source from clean source stream
        confusion_matrix, p_source = estimate_confusion_matrix(model, source_loader, device)

        # Load label-shifted stream (same subset)
        x_shift, y_shift = load_cifar10_label_shift(keep_classes=subset, n_examples=8000, shift_point=split)
        full_dataset = BasicDataset(x_shift, y_shift, transform=transform)

        test_loader = DataLoader(
            Subset(full_dataset, range(split, len(full_dataset))), batch_size=args.batch_size, shuffle=False
        )

        # 4. Estimate p_test from shifted half of the stream
        p_test = estimate_target_distribution_from_preds(model, test_loader, device)

        # 5. Create BBSE/ODS weighted protector
        protector = protect.get_bbse_ods_weighted_protector_from_ents(
            source_ents,
            p_test,
            p_source,
            source_labels,
            confusion_matrix,
            0.05,  # ods_alpha
            argparse.Namespace(gamma=1 / (8 * np.sqrt(3)), eps_clip=1.8, device=device),
        )

        # LOUIS: This is for stat tracking i guess?
        mask = torch.tensor([i in subset for i in range(10)], dtype=torch.bool)
        p_source = p_source.to("cpu") * mask
        p_source /= p_source.sum() + 1e-8

        p_test_true = protector.cdf.p_test_true.to("cpu") * mask
        p_test_true /= p_test_true.sum() + 1e-8

        # LOUIS: Here's where the problem is... i think the evaluate model logic and run martingale logic need to be
        # combined somehow, in the current setup the protector CDF cannot be updated as we go along, i think? 
        # 6) Evaluate full test stream and run martingale
        loader = DataLoader(full_dataset, batch_size=args.batch_size, shuffle=False)
        ents, acc, logits_list, labels_list = evaluate(model, loader, device)

        key = f"labelshift_{num_classes}cls_{'_'.join(map(str, subset))}"
        result = run_martingale({key: ents}, protector)[key]

        # Record statistics
        entropy_peaks[key] = np.max(ents)
        threshold_crossed[key] = np.max(result["log_sj"]) > np.log(100)

        print("Subset:", subset)
        print("p_source:", p_source.numpy())
        print("p_test_true:", p_test_true.numpy())
        print("min p_source:", p_source.min().item(), "min p_t:", p_test_true.min().item())

    # 8) Calculate and store FPR
    n_tests = len(threshold_crossed)
    n_crossed = sum(threshold_crossed.values())
    fpr = n_crossed / n_tests
    fpr_by_size[num_classes] = fpr

    print(f"\n➡️ {n_crossed} / {n_tests} ({num_classes}-class) shifts triggered detection — FPR = {fpr:.3f}\n")

# fpr_by_size now holds clean, valid FPRs per class subset size.

In [29]:
# ----------------------------------------------------------------------
#  BBSE-ODS *streaming* evaluation
#
#  - builds the protector once on the clean half
#  - then reads the *entire* stream online:
#       • updates the CDF weights with ODS **per batch**
#       • feeds protected entropies to the martingale
# ----------------------------------------------------------------------
from itertools import combinations
import numpy as np, torch, argparse, time
from torch.utils.data import DataLoader, Subset

# ------------------------------------------------------------- knobs --
NUM_CLASSES_LIST   = [4,9,10]
SEEDS              = range(1)               # reproducibility seeds
# ---------------------------------------------------------------------




def run_labelshift_bbseods_once(model, subset, *, args, transform):
    """
    Run ONE 4-k stream (clean ⇢ label-shift) for a given class subset.
    Returns (triggered[bool], log_Sj_max[float]).
    """

    SPLIT              = 2000                  # first 2k = clean   | last 2k = label-shift
    ODS_ALPHA          = 0.05                   # EMA for ODS
    GAMMA              = 1/(8*np.sqrt(3))       # martingale γ
    EPS_CLIP           = 1.8                    # martingale ϵ-clip
    DEVICE             = device                 # ← whatever you used before
    # 1) -----------------------------------------------------------------
    x_src, y_src = load_cifar10_label_shift(
        keep_classes = subset,
        n_examples   = 2*SPLIT,
        shift_point  = SPLIT,
    )

        
    ds   = BasicDataset(x_src, y_src, transform=transform)

    # --- guard against too-short stream -----------------------------
    if len(ds) < 2*SPLIT:        # e.g. subset has few classes
        SPLIT = len(ds) // 2     # fall back to half/half

        
    dl_c = DataLoader(Subset(ds, range(0, SPLIT)),  batch_size=args.batch_size, shuffle=False)   # clean half
    dl_s = DataLoader(Subset(ds, range(SPLIT, 2*SPLIT)), batch_size=args.batch_size, shuffle=False) # shift half
    dl_full = DataLoader(ds, batch_size=args.batch_size, shuffle=False)   # full 0-8000 stream

    # 2)  collect clean entropies + true labels --------------------------
    ents_clean, true_lbls = [], []
    with torch.no_grad():
        for xb, yb in dl_c:
            pr   = torch.softmax(model(xb.to(DEVICE)), 1)
            ents_clean.extend((-torch.sum(pr*torch.log(pr+1e-8), 1)).cpu().tolist())
            true_lbls.extend(yb.cpu().tolist())

    # 3)  confusion matrix + source p(y) ---------------------------------
    C, p_s = estimate_confusion_matrix(model, dl_c, DEVICE)

    # 4)  initial target p_test (predicted) -------------------------------
    p_t_pred = estimate_target_distribution_from_preds(model, dl_s, DEVICE)

    # 5)  build protector -------------------------------------------------
    cdf = BBSEODSWeightedCDF(
        entropies        = ents_clean,
        p_test           = p_t_pred,
        p_source         = p_s,
        source_labels    = true_lbls,
        confusion_matrix = C,
        ods_alpha        = ODS_ALPHA,
        device           = DEVICE,
        num_classes      = 10,
    )
    protector = protect.Protector(cdf=cdf, device=DEVICE)   # unchanged POEM class
    protector.set_gamma(GAMMA)
    protector.set_eps_clip_val(EPS_CLIP)

    # 6)  stream ----------------------------------------------------------
    log_sj, triggered, detect_pos = [], False, None
    idx = 0
    for xb, _ in dl_full:
        xb   = xb.to(DEVICE)
        pr   = torch.softmax(model(xb), 1)
        ents = (-torch.sum(pr*torch.log(pr+1e-8), 1)).cpu().tolist()
        yhat = torch.argmax(pr, 1).cpu().tolist()

        # 5a) ODS update *before* protector sees the next entropy(s)
        cdf.batch_ods_update(yhat)

        # 5b) martingale step for each sample in the batch
        for e in ents:
            log_val = martingale_step(e, protector)
            log_sj.append(log_val)

            if not triggered and log_val > np.log(100):
                triggered  = True
                detect_pos = idx        # 0-based position in full stream
            idx += 1

    delay = None
    if triggered:
        delay = detect_pos - split        # ≥0 samples after shift-point

    return triggered, delay, log_sj       # log_sj handy for debugging / plotting


def evaluate_fpr_bbseods(
    *,
    model,
    args,
    transform,
    seeds          = range(5),
    subset_sizes   = (1,2,3,4,5,6,7,8,9),
):
    rng_state = torch.random.get_rng_state()
    fprs = {k: [] for k in subset_sizes}

    for sd in seeds:
        np.random.seed(sd);  torch.manual_seed(sd)
        for k in subset_sizes:
            crosses = []
            for subset in combinations(range(10), k):
                trig, _delay, _ = run_labelshift_bbseods_once(
                    model, subset,
                    args=args, transform=transform
                )
                crosses.append(trig)
            fprs[k].append(np.mean(crosses))

    torch.random.set_rng_state(rng_state)    # restore if you like
    return {k: float(np.mean(v)) for k,v in fprs.items()}

    # ------------------- summary print ----------------------------------
    print("\n📊  BBSE-ODS FPR across seeds")
    for k in NUM_CLASSES_LIST:
        print(f"{k:2d} classes : {np.mean(fprs[k]):.3f} ± {np.std(fprs[k]):.3f}")
    return {k: float(np.mean(v)) for k, v in fprs.items()}

In [30]:
from weighted_cdf_bbse_ods import *

In [39]:
# bbseods_fpr.py -----------------------------------------------------------
from itertools import combinations
import numpy as np, torch, argparse
from torch.utils.data import DataLoader, Subset
from utilities import *

from weighted_cdf_bbse_ods   import (
    BBSEODSWeightedCDF,
    estimate_confusion_matrix,
    estimate_target_distribution_from_preds,
)

# ------------------------------------------------------------- knobs --
SPLIT              = 2000          # clean 2k • shift 2k
ODS_ALPHA          = 0.05
GAMMA              = 1/(8*np.sqrt(3))
EPS_CLIP           = 1.8
THRESH_LOG_S       = np.log(100)
# ---------------------------------------------------------------------

DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")


@torch.no_grad()
def run_labelshift_bbseods_once(
    model,
    subset,                       # e.g. (0,3,7)
    *,
    args,
    transform,
):
    """
    One clean→label-shift stream for a given subset.
    Returns (triggered, delay, log_sj_list).
    """
    # 1) -----------------------------------------------------------------
    x_all, y_all = load_cifar10_label_shift(
        keep_classes = subset,
        n_examples   = 2*SPLIT,
        shift_point  = SPLIT,
    )
    ds = BasicDataset(x_all, y_all, transform=transform)

    # in case subset has too few samples
    split = min(SPLIT, len(ds)//2)

    dl_clean = DataLoader(Subset(ds, range(0, split)),
                          batch_size=args.batch_size, shuffle=False)
    dl_shift = DataLoader(Subset(ds, range(split, 2*split)),
                          batch_size=args.batch_size, shuffle=False)
    dl_full  = DataLoader(ds, batch_size=args.batch_size, shuffle=False)

    # 2)  clean entropies + **true** labels --------------------------------
    ents_clean, true_lbls = [], []
    for xb, yb in dl_clean:
        pr = torch.softmax(model(xb.to(DEVICE)), 1)
        ents_clean.extend((-torch.sum(pr*torch.log(pr+1e-8), 1)).cpu().tolist())
        true_lbls.extend(yb.cpu().tolist())

    # 3)  confusion + p_s ---------------------------------------------------
    C, p_s = estimate_confusion_matrix(model, dl_clean, DEVICE)

    # 4)  predicted p_t -----------------------------------------------------
    p_t_pred = estimate_target_distribution_from_preds(model, dl_shift, DEVICE)

    # 5)  protector with BBSE-ODS CDF --------------------------------------
    cdf = BBSEODSWeightedCDF(
        entropies        = ents_clean,
        p_test           = p_t_pred,
        p_source         = p_s,
        source_labels    = true_lbls,
        confusion_matrix = C,
        ods_alpha        = ODS_ALPHA,
        device           = DEVICE,
        num_classes      = 10,
    )
    protector = protect.Protector(cdf=cdf, device=DEVICE)
    protector.set_gamma(GAMMA)
    protector.set_eps_clip_val(EPS_CLIP)
    protector.reset()


    # DEBUG
    print(f"[INIT] subset={subset}  "
        f"min w={cdf.weights.min():.3f}  max w={cdf.weights.max():.3f}")
    print("[INIT]  p_s:", p_s.cpu().numpy().round(3))
    print("[INIT]  p_t^pred:", p_t_pred.cpu().numpy().round(3))
    print("[INIT]  p_t^true:", cdf.p_test_true.cpu().numpy().round(3), '\n')

    # 6)  stream loop -------------------------------------------------------
    log_sj, triggered, detect_pos = [], False, None
    idx = 0
    for xb, _ in dl_full:
        xb   = xb.to(DEVICE)
        pr   = torch.softmax(model(xb), 1)
        ents = (-torch.sum(pr*torch.log(pr+1e-8), 1)).cpu().tolist()
        yhat = torch.argmax(pr, 1).cpu().tolist()

        cdf.batch_ods_update(yhat)          # online calibration
        
        LOG_EVERY = 5

        for e in ents:
            lj = martingale_step(e, protector)
            log_sj.append(lj)

            if idx % LOG_EVERY == 0:
                print(f"[{idx:4}] log S={lj:6.2f}  "
                    f"ε={protector.epsilons[-1]:5.2f}  "
                    f"γ={protector.gamma:5.3f}")
                
            if triggered:
                delay = detect_pos - split if triggered else None
                print(f"\n>>>  TRIGGER at sample {detect_pos} "
                    f"(delay = {delay} after shift) "
                    f"log S* = {log_sj[detect_pos]:.2f}\n")

            if not triggered and lj > THRESH_LOG_S:
                triggered, detect_pos = True, idx
            idx += 1

    delay = detect_pos - split if triggered else None
    return triggered, delay, log_sj


def evaluate_fpr_bbseods(
    *,
    model,
    args,
    transform,
    seeds          = range(3),
    subset_sizes   = (3),
):
    """
    Returns dict {k : mean FPR over `seeds`}
    """
    fprs = {k: [] for k in subset_sizes}
    for sd in seeds:
        np.random.seed(sd); torch.manual_seed(sd)
        for k in subset_sizes:
            crosses = []
            for subset in combinations(range(10), k):
                trig, _delay, _ = run_labelshift_bbseods_once(
                    model, subset, args=args, transform=transform
                )
                crosses.append(trig)
            fprs[k].append(np.mean(crosses))

    return {k : float(np.mean(v)) for k,v in fprs.items()}

In [ ]:
args      = argparse.Namespace(batch_size=256)

model = model.to(DEVICE).eval()   # your pre-trained ResNet-32

fpr = evaluate_fpr_bbseods(
    model     = model,
    args      = args,
    transform = transform,
    seeds     = range(1),          # or 3/5 etc.
    subset_sizes = (4, 9, 10),     # <-- matches your earlier knob
)

print("Mean FPR:")
for k,v in fpr.items():
    print(f"{k}-class → {v:.3f}")

2025-05-22 14:16:11.444 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 14:16:11.445 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


[INIT] subset=(0, 1, 2, 3)  min w=0.100  max w=2.650
[INIT]  p_s: [0.098 0.099 0.098 0.1   0.099 0.092 0.108 0.096 0.108 0.102]
[INIT]  p_t^pred: [0.245 0.246 0.232 0.226 0.012 0.018 0.006 0.003 0.008 0.004]
[INIT]  p_t^true: [0.26  0.254 0.235 0.244 0.002 0.002 0.003 0.001 0.    0.   ] 

[   0] log S=  0.00  ε=-0.07  γ=0.072
[   5] log S=  0.01  ε=-0.12  γ=0.072
[  10] log S= -0.06  ε=-0.04  γ=0.072
[  15] log S= -0.08  ε=-0.04  γ=0.072
[  20] log S= -0.08  ε=-0.07  γ=0.072
[  25] log S= -0.07  ε=-0.08  γ=0.072
[  30] log S=  0.00  ε=-0.12  γ=0.072
[  35] log S= -0.02  ε=-0.11  γ=0.072
[  40] log S=  0.01  ε=-0.12  γ=0.072
[  45] log S=  0.18  ε=-0.17  γ=0.072
[  50] log S=  0.11  ε=-0.15  γ=0.072
[  55] log S=  0.13  ε=-0.16  γ=0.072
[  60] log S= -0.06  ε=-0.11  γ=0.072
[  65] log S= -0.15  ε=-0.09  γ=0.072
[  70] log S= -0.23  ε=-0.05  γ=0.072
[  75] log S= -0.23  ε=-0.06  γ=0.072
[  80] log S= -0.18  ε=-0.08  γ=0.072
[  85] log S= -0.20  ε=-0.08  γ=0.072
[  90] log S= -0.19  ε=-0.

2025-05-22 14:16:45.639 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 14:16:45.639 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


[INIT] subset=(0, 1, 2, 4)  min w=0.100  max w=2.610
[INIT]  p_s: [0.098 0.099 0.098 0.1   0.099 0.092 0.108 0.096 0.108 0.102]
[INIT]  p_t^pred: [0.24  0.24  0.236 0.008 0.244 0.006 0.005 0.002 0.01  0.008]
[INIT]  p_t^true: [0.256 0.25  0.242 0.001 0.247 0.    0.005 0.    0.    0.   ] 

[   0] log S=  0.00  ε=-0.07  γ=0.072
[   5] log S=  0.01  ε=-0.12  γ=0.072
[  10] log S= -0.06  ε=-0.04  γ=0.072
[  15] log S= -0.08  ε=-0.04  γ=0.072
[  20] log S= -0.08  ε=-0.07  γ=0.072
[  25] log S= -0.07  ε=-0.08  γ=0.072
[  30] log S=  0.00  ε=-0.12  γ=0.072
[  35] log S= -0.02  ε=-0.11  γ=0.072
[  40] log S=  0.01  ε=-0.12  γ=0.072
[  45] log S=  0.18  ε=-0.17  γ=0.072
[  50] log S=  0.11  ε=-0.15  γ=0.072
[  55] log S=  0.13  ε=-0.16  γ=0.072
[  60] log S= -0.06  ε=-0.11  γ=0.072
[  65] log S= -0.15  ε=-0.09  γ=0.072
[  70] log S= -0.23  ε=-0.05  γ=0.072
[  75] log S= -0.23  ε=-0.06  γ=0.072
[  80] log S= -0.18  ε=-0.08  γ=0.072
[  85] log S= -0.20  ε=-0.08  γ=0.072
[  90] log S= -0.19  ε=-0.

2025-05-22 14:17:19.884 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 14:17:19.885 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


...

[INIT] subset=(0, 4, 5, 8)  min w=0.100  max w=2.702
[INIT]  p_s: [0.098 0.099 0.098 0.1   0.099 0.092 0.108 0.096 0.108 0.102]
[INIT]  p_t^pred: [0.241 0.002 0.014 0.023 0.242 0.224 0.002 0.004 0.244 0.004]
[INIT]  p_t^true: [0.256 0.003 0.    0.002 0.247 0.25  0.001 0.001 0.24  0.   ] 

[   0] log S=  0.00  ε=-0.07  γ=0.072
[   5] log S=  0.01  ε=-0.12  γ=0.072
[  10] log S= -0.06  ε=-0.04  γ=0.072
[  15] log S= -0.08  ε=-0.04  γ=0.072
[  20] log S= -0.08  ε=-0.07  γ=0.072
[  25] log S= -0.07  ε=-0.08  γ=0.072
[  30] log S=  0.00  ε=-0.12  γ=0.072
[  35] log S= -0.02  ε=-0.11  γ=0.072
[  40] log S=  0.01  ε=-0.12  γ=0.072
[  45] log S=  0.18  ε=-0.17  γ=0.072
[  50] log S=  0.11  ε=-0.15  γ=0.072
[  55] log S=  0.13  ε=-0.16  γ=0.072
[  60] log S= -0.06  ε=-0.11  γ=0.072
[  65] log S= -0.15  ε=-0.09  γ=0.072
[  70] log S= -0.23  ε=-0.05  γ=0.072
[  75] log S= -0.23  ε=-0.06  γ=0.072
[  80] log S= -0.18  ε=-0.08  γ=0.072
[  85] log S= -0.20  ε=-0.08  γ=0.072
[  90] log S= -0.19  ε=-0.

2025-05-22 14:54:53.323 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 14:54:53.323 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


[INIT] subset=(0, 4, 5, 9)  min w=0.100  max w=2.653
[INIT]  p_s: [0.098 0.099 0.098 0.1   0.099 0.092 0.108 0.096 0.108 0.102]
[INIT]  p_t^pred: [0.243 0.004 0.01  0.024 0.246 0.218 0.002 0.003 0.009 0.24 ]
[INIT]  p_t^true: [0.26  0.001 0.    0.004 0.25  0.24  0.001 0.    0.    0.243] 

[   0] log S=  0.00  ε=-0.07  γ=0.072
[   5] log S=  0.01  ε=-0.12  γ=0.072
[  10] log S= -0.06  ε=-0.04  γ=0.072
[  15] log S= -0.08  ε=-0.04  γ=0.072
[  20] log S= -0.08  ε=-0.07  γ=0.072
[  25] log S= -0.07  ε=-0.08  γ=0.072
[  30] log S=  0.00  ε=-0.12  γ=0.072
[  35] log S= -0.02  ε=-0.11  γ=0.072
[  40] log S=  0.01  ε=-0.12  γ=0.072
[  45] log S=  0.18  ε=-0.17  γ=0.072
[  50] log S=  0.11  ε=-0.15  γ=0.072
[  55] log S=  0.13  ε=-0.16  γ=0.072
[  60] log S= -0.06  ε=-0.11  γ=0.072
[  65] log S= -0.15  ε=-0.09  γ=0.072
[  70] log S= -0.23  ε=-0.05  γ=0.072
[  75] log S= -0.23  ε=-0.06  γ=0.072
[  80] log S= -0.18  ε=-0.08  γ=0.072
[  85] log S= -0.20  ε=-0.08  γ=0.072
[  90] log S= -0.19  ε=-0.

2025-05-22 14:55:28.391 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 14:55:28.392 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


[INIT] subset=(0, 4, 6, 7)  min w=0.100  max w=2.590
[INIT]  p_s: [0.098 0.099 0.098 0.1   0.099 0.092 0.108 0.096 0.108 0.102]
[INIT]  p_t^pred: [0.236 0.    0.016 0.01  0.248 0.009 0.24  0.233 0.007 0.002]
[INIT]  p_t^true: [0.254 0.001 0.004 0.001 0.252 0.    0.247 0.242 0.    0.   ] 

[   0] log S=  0.00  ε=-0.07  γ=0.072
[   5] log S=  0.01  ε=-0.12  γ=0.072
[  10] log S= -0.06  ε=-0.04  γ=0.072
[  15] log S= -0.08  ε=-0.04  γ=0.072
[  20] log S= -0.08  ε=-0.07  γ=0.072
[  25] log S= -0.07  ε=-0.08  γ=0.072
[  30] log S=  0.00  ε=-0.12  γ=0.072
[  35] log S= -0.02  ε=-0.11  γ=0.072
[  40] log S=  0.01  ε=-0.12  γ=0.072
[  45] log S=  0.18  ε=-0.17  γ=0.072
[  50] log S=  0.11  ε=-0.15  γ=0.072
[  55] log S=  0.13  ε=-0.16  γ=0.072
[  60] log S= -0.06  ε=-0.11  γ=0.072
[  65] log S= -0.15  ε=-0.09  γ=0.072
[  70] log S= -0.23  ε=-0.05  γ=0.072
[  75] log S= -0.23  ε=-0.06  γ=0.072
[  80] log S= -0.18  ε=-0.08  γ=0.072
[  85] log S= -0.20  ε=-0.08  γ=0.072
[  90] log S= -0.19  ε=-0.

In [6]:
# ──────────────────────────────────────────────────────────────────────────────
#  Covariate-shift evaluation with BBSE-ODS CDF (no PBRS)
# ──────────────────────────────────────────────────────────────────────────────
import numpy as np, torch
from collections import defaultdict
from torch.utils.data import DataLoader, Subset
from itertools       import combinations

# ---- import your helpers -----------------------------------------------------
from weighted_cdf_bbse_ods import (BBSEODSWeightedCDF,
                                   estimate_confusion_matrix,
                                   estimate_target_distribution_from_preds)



def evaluate_tpr_covshift_bbseods(
        *,                            # use only keyword args for clarity
        model,
        load_clean_then_corrupt_sequence,
        BasicDataset,
        transform,
        args,
        device,
        corruption_types      = ('gaussian_noise', 'brightness', 'fog'),
        severities            = (1, 2, 3, 4, 5),
        split                 = 2000,          # clean split-point (same as PBRS fn)
        seeds                 = range(3),
        ods_alpha             = 0.05,          # EMA for ODS
        gamma                 = 1/(8*np.sqrt(3)),
        eps_clip              = 1.8,
        log_path              = None           # optional CSV
):
    """
    True-positive (covariate-shift) evaluation *with BBSE+ODS weighted CDF*.
    Returns: dict[(corr,sev)] -> {detection_rate, avg_delay, raw_detections, raw_delays}
    """
    DEVICE  = device
    label   = "BBSE-ODS"
    results = defaultdict(dict)

    for corruption in corruption_types:
        for sev in severities:
            detections, delays = [], []

            for sd in seeds:
                # reproducibility ------------------------------------------------
                np.random.seed(sd);  torch.manual_seed(sd)
                torch.backends.cudnn.deterministic = True
                torch.backends.cudnn.benchmark     = False

                # 1) stream loader (clean ▸ corrupt) -----------------------------
                loader, _, _ = load_clean_then_corrupt_sequence(
                    corruption = corruption,
                    severity   = sev,
                    n_examples = split,          # function doubles internally: 2*split total
                    data_dir   = "./data",
                    transform  = transform,
                    batch_size = args.batch_size,
                )

                # loader.dataset length = 2*split
                dl_clean = DataLoader(
                    Subset(loader.dataset, range(0,        split)),
                    batch_size = args.batch_size, shuffle=False)
                dl_shift = DataLoader(
                    Subset(loader.dataset, range(split, 2*split)),
                    batch_size = args.batch_size, shuffle=False)

                # 2) collect clean entropies + labels ---------------------------
                ents_clean, y_clean = [], []
                with torch.no_grad():
                    for xb, yb in dl_clean:
                        pr = torch.softmax(model(xb.to(DEVICE)), 1)
                        ents_clean.extend((-torch.sum(pr*torch.log(pr+1e-8), 1)).cpu().tolist())
                        y_clean.extend(yb.cpu().tolist())

                # 3) confusion matrix + p_source -------------------------------
                C, p_source = estimate_confusion_matrix(model, dl_clean, DEVICE)

                # 4) initial p_test (predicted) on the *shift* half ------------
                p_t_pred = estimate_target_distribution_from_preds(model, dl_shift, DEVICE)

                # 5) build BBSE-ODS weighted CDF -------------------------------
                cdf = BBSEODSWeightedCDF(
                    entropies        = ents_clean,
                    p_test           = p_t_pred,
                    p_source         = p_source,
                    source_labels    = y_clean,
                    confusion_matrix = C,
                    ods_alpha        = ods_alpha,
                    device           = DEVICE,
                    num_classes      = 10,
                )

                protector = protect.Protector(cdf=cdf, device=DEVICE)
                protector.set_gamma(gamma)
                protector.set_eps_clip_val(eps_clip)

                # 6) full stream pass + online martingale ----------------------
                triggered, delay = False, None
                log_sj, idx = [], 0
                for xb, _ in loader:
                    xb   = xb.to(DEVICE)
                    pr   = torch.softmax(model(xb), 1)
                    ents = (-torch.sum(pr*torch.log(pr+1e-8), 1)).cpu().tolist()
                    yhat = torch.argmax(pr, 1).cpu().tolist()

                    # ODS update before using the new entropies
                    cdf.batch_ods_update(yhat)

                    for e in ents:
                        log_val = martingale_step(e, protector)
                        log_sj.append(log_val)

                        if not triggered and log_val > np.log(100):
                            triggered = True
                            detect_pos = idx
                        idx += 1

                if triggered:
                    delay = detect_pos - split          # ≥0 samples after shift-point

                detections.append(int(triggered))
                delays.append(delay)

            # ------- aggregate over seeds -------------------------------------
            det_rate = float(np.mean(detections))
            avg_del  = (float(np.mean([d for d in delays if d is not None]))
                        if any(d is not None for d in delays) else None)

            print(f"[{label}] {corruption} s{sev}: "
                  f"detected {sum(detections)}/{len(seeds)} | delay={avg_del}")

            results[(corruption, sev)] = dict(
                detection_rate = det_rate,
                avg_delay      = avg_del,
                raw_detections = detections,
                raw_delays     = delays,
            )

    # optional CSV -------------------------------------------------------------
    if log_path is not None:
        import pandas as pd, os
        rows = []
        for (c, s), v in results.items():
            rows.append(dict(Corruption=c, Severity=s, Method=label,
                             DetRate=v['detection_rate'], AvgDelay=v['avg_delay']))
        mode = 'a' if os.path.exists(log_path) else 'w'
        pd.DataFrame(rows).to_csv(log_path, mode=mode, header=(mode=='w'), index=False)
        print(f"↳ logged to {log_path}")

    return results

In [14]:
res_bbseods = evaluate_tpr_covshift_bbseods(model=model,load_clean_then_corrupt_sequence=load_clean_then_corrupt_sequence, BasicDataset=BasicDataset, transform=transform, args=args, device=device)

Files already downloaded and verified


2025-05-22 14:59:12.818 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 14:59:12.819 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


Files already downloaded and verified


2025-05-22 14:59:41.227 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 14:59:41.227 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


Files already downloaded and verified


...

Files already downloaded and verified


2025-05-22 15:19:20.290 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 15:19:20.291 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


Files already downloaded and verified


2025-05-22 15:19:48.034 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 15:19:48.034 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


[BBSE-ODS] fog s5: detected 3/3 | delay=210.0


In [19]:
CORRUPTIONS = tuple(c for c in ('shot_noise', 'motion_blur', 'snow', 'pixelate', 'gaussian_noise', 'defocus_blur', 'brightness', 'fog', 'zoom_blur', 'frost', 'glass_blur', 'impulse_noise', 'contrast', 'jpeg_compression', 'elastic_transform') if c not in ('gaussian_noise', 'brightness', 'fog'))

In [20]:
res_bbseods = evaluate_tpr_covshift_bbseods(model=model,load_clean_then_corrupt_sequence=load_clean_then_corrupt_sequence, BasicDataset=BasicDataset, transform=transform, args=args, device=device, corruption_types=CORRUPTIONS)

Files already downloaded and verified


2025-05-22 17:15:51.370 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 17:15:51.371 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


Files already downloaded and verified


2025-05-22 17:16:18.332 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 17:16:18.332 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


Files already downloaded and verified


...

Files already downloaded and verified


2025-05-22 18:38:18.312 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 18:38:18.313 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


Files already downloaded and verified


2025-05-22 18:38:45.986 | INFO     | protector:set_gamma:47 - setting gamma val to 0.07216878364870323
2025-05-22 18:38:45.987 | INFO     | protector:set_eps_clip_val:43 - setting epsilon clip val to 1.8


[BBSE-ODS] elastic_transform s5: detected 3/3 | delay=217.0


True positive rate

In [ ]:
accs, entropy_streams, logits_list_dict, logits_labels_dict = {}, {}, {}, {}
results = {}
corruptions = CORRUPTIONS if args.all_corruptions else [args.corruption]

use_pbrs = False
confidence_threshold = 0.8  # You can tune this

for corruption in corruptions:
    for severity in range(1, 6):
        print(f"🔎 {corruption} severity {severity} (clean → corrupt)")

        # Load clean-to-corrupt stream
        loader, is_clean, labels = load_clean_then_corrupt_sequence(
            corruption=corruption,
            severity=severity,
            n_examples=4000,
            data_dir="./data",
            transform=transform,
            batch_size=args.batch_size,
        )

        if use_pbrs:
            buffer = PBRSBuffer(capacity=512, num_classes=10)

        logits_list = []
        labels_list = []
        entropy_list = []

        with torch.no_grad():
            for x_batch, y_batch in loader:
                x_batch, y_batch = x_batch.to(device), y_batch.to(device)
                logits = model(x_batch)
                probs = torch.softmax(logits, dim=1)
                entropies = -torch.sum(probs * torch.log(probs + 1e-8), dim=1)
                pseudo_labels = torch.argmax(probs, dim=1)
                max_probs = torch.max(probs, dim=1).values

                for entropy, y_hat, conf in zip(
                    entropies.cpu().tolist(), pseudo_labels.cpu().tolist(), max_probs.cpu().tolist()
                ):
                    if use_pbrs:
                        if confidence_accept(conf, threshold=0.8, softness=15) and buffer.accept(y_hat):
                            buffer.add(None, entropy, y_hat)
                    else:
                        entropy_list.append(entropy)

                logits_list.append(logits.cpu())
                labels_list.append(y_batch.cpu())

        key = f"{corruption}_s{severity}"

        # Store entropy stream
        ents = np.array(buffer.get_entropies()) if use_pbrs else np.array(entropy_list)
        entropy_streams[key] = ents
        logits_list_dict[key] = logits_list
        logits_labels_dict[key] = labels_list


# Run martingale detection on all entropy streams
results = run_martingale(entropy_streams, protector)

# Compute accuracy over time
for corruption in corruptions:
    for severity in range(1, 6):
        key = f"{corruption}_s{severity}"
        accs = compute_accuracy_over_time_from_logits(logits_list_dict[key], logits_labels_dict[key])
        results[key]["accs"] = accs